In [1]:
using DifferentialEquations
using Plots
using LinearAlgebra

In [2]:
# Parameters

L = 450e-6
C = 2.5e-3
V_dc = 1200
R = 50
;

In [ ]:
function delay_model(du,u,h,p,t)
    
    p1, p2, p3 = p
    hist2 = h(p,t-tau)[2]
    hist4 = h(p,t-tau)[4]
    du[1] = -p1 * u[2]
    du[2] = p2 * (u[1] - p3 * (hist2 - hist4))
    du[3] = -p1 * u[4]
    du[4] = p2 * (u[3] + p3 * (hist2 - hist4))
    
end

In [ ]:
A_test_1 = [0 -1/L 0 0
        1/C 0 0 0
        0 0 0 -1/L
        0 0 1/C 0]

A_test_2 = [0 0 0 0
        0 -1/(R*C) 0 1/(R*C)
        0 0 0 0
        0 1/(R*C) 0 -1/(R*C)]

f(u, h, p, t) = A_test_1*u + A_test_2*h(p, t-tau)

In [ ]:
function run_delay_sim(model,u0,h,p,t_final,lags,alg)
    
    tspan = (0.0, t_final)
    prob = DDEProblem(model,u0,h,tspan,p; constant_lags=lags)
    sol = solve(prob,alg)
    
    return sol 
end

In [8]:
p1 = 1/L; p2 = 1/C; p3 = 1/R
p = (p1, p2, p3)

alg = MethodOfSteps(Rosenbrock23());

u0 = ones(4)
h(p,t) = ones(4)

t_final = 10.0
tau = 100
lags = [tau]
;

In [ ]:
sol = run_delay_sim(f,u0,h,p,t_final,lags,alg);

In [ ]:
plot(sol)

In [ ]:
function no_delay_model(du,u,p,t)
    
    p1, p2, p3 = p
    du[1] = -p1 * u[2]
    du[2] = p2 * (u[1] - p3 * (u[2] - u[4]))
    du[3] = -p1 * u[4]
    du[4] = p2 * (u[3] + p3 * (u[2] - u[4]))
    
end
;

In [3]:
function run_no_delay_sim(model,u0,p,t_final, solver)
    
    tspan = (0.0, t_final)
    prob = ODEProblem(model,u0,tspan,p)
    sol = solve(prob, solver)
    
    return sol 
end

run_no_delay_sim (generic function with 1 method)

In [9]:
u0 = 0.1*ones(4)
t_final = 10
solver = Rosenbrock23();

In [27]:
A_test = [0 -1/L 0 0
        1/C -1/(R*C) 0 1/(R*C)
        0 0 0 -1/L
        0 1/(R*C) 1/C -1/(R*C)]

B = [V_dc/2 0 
    0 0 
    0 V_dc/2 
    0 0]

m1 = t->sin(2*pi*60*t)
m2 = t->sin(2*pi*60*t + 2*pi/3)

f_no(u,p,t) = A_test*u #+ 1e6*[1;1;1;1]#+ B*vcat(m1,m2)


f_no (generic function with 1 method)

In [32]:
t_final = 100

sol = run_no_delay_sim(f_no,u0,p,t_final, solver);

In [33]:
plot(sol)

In [ ]:
eigvals(A_test)

In [ ]:
L = 450e-6
L_l = 450e-6
C = 2.5e-3
V_dc = 1200
R = 50
R_l = 1

E2 = zeros(5,5)
E2[1,1] = L
E2[2,2] = C
E2[3,3] = L_l
E2[4,4] = L
E2[5,5] = C

E2_inv = inv(E2)

A_temp0 = [0 -1 0 0 0
            1 -1/R 0 0 0
            0 1 0 0 -1
            0 0 0 0 -1
            0 0 0 1 -1/R]

A_temp1 = zeros(5,5)
A_temp[:,3] = [0; -1; -R_l; 0; 1]
A_temp = A_temp0 + A_temp1

A_dyn_line = E2_inv*A_temp

In [ ]:
include("functions.jl")
using Kronecker

In [ ]:
tau = 1
N = 7

M, n = build_M(N, tau, E2_inv*A_temp0, E2_inv*A_temp1)

In [ ]:
eigvals(M)

In [ ]:
eigvals(A_dyn_line)

In [ ]:
sqrt(1/L*C)

In [ ]:
1/ans
